In [22]:
from nltk.corpus import wordnet as wn
from nltk.corpus import brown
import nltk
from tqdm.auto import tqdm
import json

# Create a frequency distribution of words in the Brown corpus
fd = nltk.FreqDist([word.lower() for word in tqdm(brown.words())])

# Create an empty dictionary to store the entries
dictionary = {}

# Loop through all the synsets in WordNet and add an entry to the dictionary for each word
for synset in tqdm(wn.all_synsets()):
    word = synset.lemmas()[0].name()
    senses = [syn.definition() for syn in wn.synsets(word)]
    synonyms = set()
    antonyms = set()
    for lemma in synset.lemmas():
        syn_name = lemma.name()
        if syn_name != word and word not in syn_name:
            synonyms.add(syn_name)
        for antonym in lemma.antonyms():
            ant_name = antonym.name()
            if ant_name != word and word not in ant_name:
                antonyms.add(ant_name)
    word_fixed = word.replace("-","").replace("_","").replace(" ","")
    entry = {
        "word": word_fixed,
        "senses": senses,
        "synonyms": list(synonyms),
        "antonyms": list(antonyms),
        "frequency": fd[word.lower()]
    }
    dictionary[word_fixed] = entry

# Write the dictionary to a JSON file
with open('wordnet_dict_freq.json', 'w') as outfile:
    json.dump(dictionary, outfile, indent=4)


100%|██████████| 1161192/1161192 [00:02<00:00, 577463.34it/s]
117659it [00:04, 26815.49it/s]


In [21]:
import wn
from nltk.corpus import brown
import nltk
from tqdm.auto import tqdm
import json
import json

# Load the German WordNet (OdeNet) corpus
wn.download('odenet')

# Create an empty dictionary to store the entries
dictionary = {}

def remove_umlaute(s):
    s = s.replace("ß", "ss")
    s = s.replace("ü", "ue")
    s = s.replace("ö", "oe")
    s = s.replace("ä", "ae")
    s = s.replace("U", "Ue")
    s = s.replace("Ö", "Oe")
    s = s.replace("Ä", "Äe")
    return s

# Loop through all the synsets in OdeNet and add an entry to the dictionary for each word
for i, word in enumerate(tqdm(wn.words())):
    lemma = word.lemma()
    if " " in lemma or (not str(lemma).isalpha) or "-" in lemma:
        continue
    senses = [syn.definition() for syn in word.synsets()]
    senses = [s for s in senses if (s is not None and lemma not in s)]

    synonyms = set()
    antonyms = set()
    
    for synset in word.synsets():
        for w in synset.words():
            syn_name = w.lemma()
            if syn_name != lemma and lemma not in syn_name:
                syn_name = remove_umlaute(syn_name)
                synonyms.add(syn_name)
        #for antonym in lemma.antonyms():
        #    ant_name = antonym.name()
        #    if ant_name != word and word not in ant_name:
        #        antonyms.add(ant_name)
    if len(senses) > 0 or len(synonyms) > 0:
        lemma = lemma.lower()
        lemma = lemma.replace("ß", "ss")
        lemma = lemma.replace("ü", "ue")
        lemma = lemma.replace("ö", "oe")
        lemma = lemma.replace("ä", "ae")

        senses = [remove_umlaute(s) for s in senses]

        entry = {
            "word": lemma,
            "senses": senses,
            "synonyms": list(synonyms),
            "antonyms": list(antonyms),
            "frequency": len(word.translate())
        }
        dictionary[lemma.lower()] = entry

# Write the dictionary to a JSON file
with open('odenet_dict.json', 'w') as outfile:
    json.dump(dictionary, outfile, indent=4, ensure_ascii=False)



Cached file found: /home/jonas/.wn_data/downloads/5a26d97a0081996db4cd621638a8a9b0da09aa25
Skipping odenet:1.4 (Offenes Deutsches WordNet); already added

100%|██████████| 120107/120107 [01:34<00:00, 1272.74it/s]


In [4]:
l = wn.words()[10101]
l.lemma()

'Unverschämtheit'

In [5]:
l.senses()

[Sense('w10166_2106-n'), Sense('w10166_3207-n'), Sense('w10166_33225-n')]

In [6]:
s = l.synsets()[0]

In [113]:
s.definition()

'unangebrachte Verspieltheit'

In [7]:
sense = l.senses()[0]

In [139]:
dictionary

{'kernspaltung': {'word': 'kernspaltung',
  'senses': ['eine Kernreaktion, bei der ein massiver Kern unter gleichzeitiger Freisetzung von Energie in kleinere Kerne gespalten wird'],
  'synonyms': ['Atomspaltung', 'Kernfission', 'Fission'],
  'antonyms': []},
 'kernfission': {'word': 'kernfission',
  'senses': ['eine Kernreaktion, bei der ein massiver Kern unter gleichzeitiger Freisetzung von Energie in kleinere Kerne gespalten wird'],
  'synonyms': ['Kernspaltung', 'Atomspaltung', 'Fission'],
  'antonyms': []},
 'atomspaltung': {'word': 'atomspaltung',
  'senses': ['eine Kernreaktion, bei der ein massiver Kern unter gleichzeitiger Freisetzung von Energie in kleinere Kerne gespalten wird'],
  'synonyms': ['Kernspaltung', 'Kernfission', 'Fission'],
  'antonyms': []},
 'fission': {'word': 'fission',
  'senses': ['eine Kernreaktion, bei der ein massiver Kern unter gleichzeitiger Freisetzung von Energie in kleinere Kerne gespalten wird',
   'der Prozess der Reproduktion und des Wachstums, b